# Рекуррентные нейронные сети

## Читаем данные

In [ ]:
import numpy as np,tensorflow as tf

import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (10,10)
legend_fontsize = 16

In [ ]:
def load_data(filename, seq_len, normalise_window):
    data = [ float(x) for x in open(filename)]

    sequence_length = seq_len + 1
    result = []
    for index in range(len(data) - sequence_length):
        result.append(data[index: index + sequence_length])
    
    if normalise_window:
        result = normalise_windows(result)

    result = np.array(result)

    row = round(0.9 * result.shape[0])
    train = result[:int(row), :]
    np.random.shuffle(train)
    x_train = train[:, :-1]
    y_train = train[:, -1]
    x_test = result[int(row):, :-1]
    y_test = result[int(row):, -1]

    x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))
    x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))  

    return [x_train, y_train, x_test, y_test]

x_train, y_train, x_test, y_test = load_data('sinwave.csv', 50, False)
plt.plot(y_test)
plt.show()

In [ ]:
x_train

## Строим модель

In [ ]:
from keras.datasets import mnist
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten, BatchNormalization
from keras.layers.recurrent import LSTM
from keras.utils import np_utils
from keras import callbacks
from keras import optimizers, regularizers
# tf.python.control_flow_ops = tf

In [ ]:
model = Sequential()

model.add(LSTM(input_dim=1, units=50, return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(100, return_sequences=False))
model.add(Dropout(0.2))
model.add(Dense(output_dim=1))
model.add(Activation("linear"))

model.compile(loss="mse", optimizer="adam")

In [ ]:
model.fit( x_train, y_train, batch_size=512, nb_epoch=10, validation_split=0.05)

## Предсказываем

### Предсказываем только следующую точку

In [ ]:
def predict_point_by_point(model, data):
    predicted = model.predict(data)
    predicted = np.reshape(predicted, (predicted.size,))
    return predicted

predicted = predict_point_by_point(model, x_test)
plt.plot(y_test)
plt.plot(predicted)
plt.show()

### Предсказываем надолго в будущее

In [ ]:
def predict_sequence_full(model, data, window_size):
    curr_frame = data[0]
    predicted = []
    for i in range(len(data)):
        predicted.append(model.predict(curr_frame[np.newaxis,:,:])[0,0])
        curr_frame = curr_frame[1:]
        curr_frame = np.insert(curr_frame, [window_size-1], predicted[-1], axis=0)
    return predicted

predicted = predict_sequence_full(model, x_test, 50)
plt.plot(y_test)
plt.plot(predicted)
plt.show()

# Попробуем что-то более сложное

In [ ]:
def normalise_windows(window_data):
    normalised_data = []
    for window in window_data:
        normalised_window = [((float(p) / float(window[0])) - 1) for p in window]
        normalised_data.append(normalised_window)
    return normalised_data

x_train, y_train, x_test, y_test = load_data('sp500.csv', 50, True)
plt.plot(y_test)
plt.show()

In [ ]:
plt.plot(y_train)
plt.show()

In [ ]:
model = Sequential()

model.add(LSTM(input_dim=1, output_dim=50, return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(100, return_sequences=False))
model.add(Dropout(0.2))
model.add(Dense(output_dim=1))
model.add(Activation("linear"))
# TimeDistributedDense
model.compile(loss="mse", optimizer="adam")

In [ ]:
model.fit( x_train, y_train, batch_size=512, nb_epoch=100, validation_split=0.05)

In [ ]:
predicted = predict_point_by_point(model, x_test)
plt.plot(y_test)
plt.plot(predicted)
plt.show()

In [ ]:
predicted = predict_sequence_full(model, x_test, 50)
plt.plot(y_test)
plt.plot(predicted)
plt.show()

In [ ]:
def predict_sequences_multiple(model, data, window_size, prediction_len):
    prediction_seqs = []
    for i in range(int(len(data)/prediction_len)):
        curr_frame = data[i*prediction_len]
        predicted = []
        for j in range(prediction_len):
            predicted.append(model.predict(curr_frame[np.newaxis,:,:])[0,0])
            curr_frame = curr_frame[1:]
            curr_frame = np.insert(curr_frame, [window_size-1], predicted[-1], axis=0)
        prediction_seqs.append(predicted)
    return prediction_seqs

predicted = predict_sequences_multiple(model, x_test, 50, 50)
plt.plot(y_test)
for i, data in enumerate(predicted):
    padding = [None for p in range(i * 50)]
    plt.plot(padding + data)
plt.show()